HELOC - Classification Model

Introduction and Project Outline:
- Our goal is to predict the classification label of unseen customer data - either approved or denied for Home Equity Lines of Credit based on certain customer attributes in their application using the Huggingface HELOC dataset.

Business Application and Impact: 
- We want to determine whether we can improve the application response time as well as maximizing the 'goods' and minimizing the 'bads' to have a positive impact on revenue generation. 
- Impacts would be optimizing the business processes, saving time and money, and reducing employee workload freeing them up for other tasks.
- Based on our research, loan applications used to be approved at the sole discretion of a Loan Officer. This person based their entire decision on whether to approve or deny a loan on their past experience and their implicit bias which could lead to misclassificiation of applicants. 
- If our model is good at classifying the rejected applications based on concrete data, then we could potentially lessen the financial impact of denying applications when they should be approved and approving applications when they should be denied. 
- This is also a much more explainable method and results could be communicated to denied applicants helping them to identify areas in which they need to improve. 
    - Ie - Needing a higher income, lowering their current debt, improving their credit score, or having a longer credit history.

Literature Review:
- Find at least two online resources such as blog posts or tutorials that provide a code-implemented project related to your topic. Summarize the key points and explain how they are relevant to your work. 
- Note that the resources should generally not be academic articles unless they include code.
- Human Learn Documentation 
    - https://koaning.github.io/human-learn/index.html
- Calmcode.io Tutorial 
    - https://calmcode.io/course/human-learn/introduction

Reference Article:
- Credit Risk Prediction - HELOC Case 
    - http://didawiki.di.unipi.it/lib/exe/fetch.php/bigdataanalytics/bda/credit_risk_prediction_heloc_case.pdf

Data Preparation:
- Data was downloaded from Huggingface
    - https://huggingface.co/datasets/mstz/heloc
- **Include any transformations, feature engineering**
- There were no missing values

Methodology:
- Models:
    - Boosted Trees: can capture complex patterns and interactions between features and effectively model non-linear relationships between variables. Boosted Trees can provide high predictive accuracy and are robust to overfitting, especially when properly tuned.
    - Logistic Regression: can be used to predict the probability of default based on various predictor variables. However, it may not capture complex non-linear relationships as effectively as other models.
    - K Nearest Neighbors: can be used to classify applicants as likely to default or not based on the characteristics of their nearest neighbors in the dataset. KNN is simple and intuitive but can be computationally expensive and may struggle with high-dimensional data.
- Methods: 
    - Hyperparameter tuning
    - Sklearn pipelines

In [39]:
%%capture
!pip install human-learn
!pip install plotly.express
!pip install --upgrade nbformat
!pip install datasets
!pip install sklearn

  Using cached datasets-2.20.0-py3-none-any.whl.metadata (19 kB)
  Using cached filelock-3.15.4-py3-none-any.whl.metadata (2.9 kB)
  Using cached pyarrow-16.1.0-cp310-cp310-win_amd64.whl.metadata (3.1 kB)
  Using cached pyarrow_hotfix-0.6-py3-none-any.whl.metadata (3.6 kB)
  Using cached dill-0.3.8-py3-none-any.whl.metadata (10 kB)
  Using cached requests-2.32.3-py3-none-any.whl.metadata (4.6 kB)
  Using cached tqdm-4.66.4-py3-none-any.whl.metadata (57 kB)
  Using cached xxhash-3.4.1-cp310-cp310-win_amd64.whl.metadata (12 kB)
  Using cached multiprocess-0.70.16-py310-none-any.whl.metadata (7.2 kB)
  Using cached fsspec-2024.5.0-py3-none-any.whl.metadata (11 kB)
  Using cached aiohttp-3.9.5-cp310-cp310-win_amd64.whl.metadata (7.7 kB)
  Using cached huggingface_hub-0.23.4-py3-none-any.whl.metadata (12 kB)
  Using cached aiosignal-1.3.1-py3-none-any.whl.metadata (4.0 kB)
  Using cached frozenlist-1.4.1-cp310-cp310-win_amd64.whl.metadata (12 kB)
  Using cached multidict-6.0.5-cp310-cp310-w

In [6]:
from datasets import load_dataset

# Load the HELOC dataset
heloc_dataset = load_dataset('mstz/heloc')
df = heloc_dataset['train'].to_pandas()

In [7]:
df

estimate_of_risk  months_since_first_trade  months_since_last_trade  \
0                    55                       144                        4   
1                    61                        58                       15   
2                    67                        66                        5   
3                    66                       169                        1   
4                    81                       333                       27   
...                 ...                       ...                      ...   
10454                73                       131                        5   
10455                65                       147                       39   
10456                74                       129                        6   
10457                72                       234                       12   
10458                66                        28                        1   

       average_duration_of_resolution  number_of_satisfactory_trades  \
0                                  84                             20   
1                                  41                              2   
2                                  24                              9   
3                                  73                             28   
4                                 132                             12   
...                               ...                            ...   
10454                              57                             21   
10455                              68                             11   
10456                              64                             18   
10457                             113                             42   
10458                              17                              4   

       nr_trades_insolvent_for_over_60_days  \
0                                         3   
1                                         4   
2                                         0   
3                                         1   
4                                         0   
...                                     ...   
10454                                     0   
10455                                     0   
10456                                     1   
10457                                     2   
10458                                     0   

       nr_trades_insolvent_for_over_90_days  percentage_of_legal_trades  \
0                                         0                          83   
1                                         4                         100   
2                                         0                         100   
3                                         1                          93   
4                                         0                         100   
...                                     ...                         ...   
10454                                     0                          95   
10455                                     0                          92   
10456                                     1                         100   
10457                                     2                          96   
10458                                     0                         100   

       months_since_last_illegal_trade  maximum_illegal_trades_over_last_year  \
0                                    2                                      3   
1                                   -7                                      0   
2                                   -7                                      7   
3                                   76                                      6   
4                                   -7                                      7   
...                                ...                                    ...   
10454                               80                                      6   
10455                               28                                      6   
10456     

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10459 entries, 0 to 10458
Data columns (total 24 columns):
 #   Column                                    Non-Null Count  Dtype
---  ------                                    --------------  -----
 0   estimate_of_risk                          10459 non-null  int8 
 1   months_since_first_trade                  10459 non-null  int32
 2   months_since_last_trade                   10459 non-null  int32
 3   average_duration_of_resolution            10459 non-null  int32
 4   number_of_satisfactory_trades             10459 non-null  int16
 5   nr_trades_insolvent_for_over_60_days      10459 non-null  int16
 6   nr_trades_insolvent_for_over_90_days      10459 non-null  int16
 7   percentage_of_legal_trades                10459 non-null  int16
 8   months_since_last_illegal_trade           10459 non-null  int32
 9   maximum_illegal_trades_over_last_year     10459 non-null  int8 
 10  maximum_illegal_trades                    10459 non-null  

In [9]:
print(df.isnull().sum())

estimate_of_risk                            0
months_since_first_trade                    0
months_since_last_trade                     0
average_duration_of_resolution              0
number_of_satisfactory_trades               0
nr_trades_insolvent_for_over_60_days        0
nr_trades_insolvent_for_over_90_days        0
percentage_of_legal_trades                  0
months_since_last_illegal_trade             0
maximum_illegal_trades_over_last_year       0
maximum_illegal_trades                      0
nr_total_trades                             0
nr_trades_initiated_in_last_year            0
percentage_of_installment_trades            0
months_since_last_inquiry_not_recent        0
nr_inquiries_in_last_6_months               0
nr_inquiries_in_last_6_months_not_recent    0
net_fraction_of_revolving_burden            0
net_fraction_of_installment_burden          0
nr_revolving_trades_with_balance            0
nr_installment_trades_with_balance          0
nr_banks_with_high_ratio          

In [10]:
print(df.describe())

       estimate_of_risk  months_since_first_trade  months_since_last_trade  \
count      10459.000000              10459.000000             10459.000000   
mean          67.425758                184.205373                 8.543455   
std           21.121621                109.683816                13.301745   
min           -9.000000                 -9.000000                -9.000000   
25%           63.000000                118.000000                 3.000000   
50%           71.000000                178.000000                 5.000000   
75%           79.000000                249.500000                11.000000   
max           94.000000                803.000000               383.000000   

       average_duration_of_resolution  number_of_satisfactory_trades  \
count                    10459.000000                   10459.000000   
mean                        73.843293                      19.428052   
std                         38.782803                      13.004327   
min      

In [13]:
# 0 = Good, 1 = Bad
y = df.is_at_risk.map({'No': 0, 'Yes': 1})

df['is_at_risk'].value_counts()

is_at_risk
1    5459
0    5000
Name: count, dtype: int64

In [14]:
X = df.drop(columns=['is_at_risk'])

Preliminary EDA

- X Variables

In [15]:
# Histogram of Estimate of Risk
import plotly.express as px
fig = px.histogram(df, x='estimate_of_risk', nbins=30, title='Distribution of Estimate of Risk')
fig.show()

In [16]:
# Histogram of Months Since First Trade
fig = px.histogram(df, x='months_since_first_trade', nbins=30, title='Distribution of Months Since First Trade')
fig.show()


In [17]:
# Histogram of Months Since Last Trade
fig = px.histogram(df, x='months_since_last_trade', nbins=30, title='Distribution of Months Since Last Trade')
fig.show()

In [18]:
# Histogram of Average Duration of Resolution
fig = px.histogram(df, x='average_duration_of_resolution', nbins=30, title='Distribution of Average Duration of Resolution')
fig.show()

In [19]:
# Histogram of Number of Satisfactory Trades
fig = px.histogram(df, x='number_of_satisfactory_trades', nbins=30, title='Distribution of Number of Satisfactory Trades')
fig.show()

In [21]:
# Histogram of NR Trades Insolvent for Over 60 Days
fig = px.histogram(df, x='nr_trades_insolvent_for_over_60_days', nbins=30, title='Distribution of NR Trades Insolvent for Over 60 Days')
fig.show()

In [22]:
# Histogram of NR Trades Insolvent for Over 90 Days
fig = px.histogram(df, x='nr_trades_insolvent_for_over_90_days', nbins=30, title='Distribution of NR Trades Insolvent for Over 90 Days')
fig.show()

In [23]:
# Histogram of Percentage of Legal Trades
fig = px.histogram(df, x='percentage_of_legal_trades', nbins=30, title='Distribution of Percentage of Legal Trades')
fig.show()

In [24]:
# Histogram of Months Since Last Illegal Trade
fig = px.histogram(df, x='months_since_last_illegal_trade', nbins=30, title='Distribution of Months Since Last Illegal Trade')
fig.show()

In [25]:
# Histogram of Maximum Illegal Trades over Last Year
fig = px.histogram(df, x='maximum_illegal_trades_over_last_year', nbins=30, title='Distribution of Maximum Illegal Trades over Last Year')
fig.show()

In [26]:
# Histogram of Maximum Illegal Trades
fig = px.histogram(df, x='maximum_illegal_trades', nbins=30, title='Distribution of Maximum Illegal Trades')
fig.show()

In [27]:
# Histogram of NR Total Trades
fig = px.histogram(df, x='nr_total_trades', nbins=30, title='Distribution of NR Total Trades')
fig.show()

In [28]:
# Histogram of NR Trades Initiated in Last Year
fig = px.histogram(df, x='nr_trades_initiated_in_last_year', nbins=30, title='Distribution of NR Trades Initiated in Last Year')
fig.show()

In [29]:
# Histogram of Percentage of Installment Trades
fig = px.histogram(df, x='percentage_of_installment_trades', nbins=30, title='Distribution of Percentage of Installment Trades')
fig.show()

In [30]:
# Histogram of Months Since Last Inquiry Not Recent
fig = px.histogram(df, x='months_since_last_inquiry_not_recent', nbins=30, title='Distribution of Months Since Last Inquiry Not Recent')
fig.show()

In [31]:
# Histogram of NR Inquiries in Last 6 Months
fig = px.histogram(df, x='nr_inquiries_in_last_6_months', nbins=30, title='NR Inquiries in Last 6 Months')
fig.show()

In [32]:
# Histogram of NR Inquiries in Last 6 Months Not Recent
fig = px.histogram(df, x='nr_inquiries_in_last_6_months_not_recent', nbins=30, title='Distribution of NR Inquiries in Last 6 Months Not Recent')
fig.show()

In [33]:
# Histogram of Net Fraction of Revolving Burden
fig = px.histogram(df, x='net_fraction_of_revolving_burden', nbins=30, title='Distribution of Net Fraction of Revolving Burden')
fig.show()

In [34]:
# Histogram of Net Fraction of Installment Burden
fig = px.histogram(df, x='net_fraction_of_installment_burden', nbins=30, title='Distribution of Net Fraction of Installment Burden')
fig.show()

In [35]:
# Histogram of NR Revolving Trades with Balance
fig = px.histogram(df, x='nr_revolving_trades_with_balance', nbins=30, title='Distribution of NR Revolving Trades with Balance')
fig.show()

In [36]:
# Histogram of NR Installment Trades with Balance
fig = px.histogram(df, x='nr_installment_trades_with_balance', nbins=30, title='Distribution of NR Installment Trades with Balance')
fig.show()

In [37]:
# Histogram of NR Banks with High Ratio
fig = px.histogram(df, x='nr_banks_with_high_ratio', nbins=30, title='Distribution of NR Banks with High Ratio')
fig.show()

In [38]:
# Histogram of Percentage Trades with Balance
fig = px.histogram(df, x='percentage_trades_with_balance', nbins=30, title='Distribution of Percentage Trades with Balance')
fig.show()

- Y Variable

In [45]:
#Count plot of 'Is at Risk'
counts = df['is_at_risk'].value_counts().reset_index()
counts.columns = ['is_at_risk', 'count']

# Create the count plot
fig = px.bar(counts, x='is_at_risk', y='count', 
             labels={'is_at_risk': 'Is at Risk', 'count': 'Count'}, 
             title='Count Plot of "Is at Risk" Variable')

# Update the x-axis labels
fig.update_xaxes(
    tickvals=[0, 1],
    ticktext=['No', 'Yes']
)

fig.show()

In [51]:
fig = px.scatter(df, x="percentage_of_legal_trades", y="months_since_first_trade", color="is_at_risk")
fig.show()

In [49]:
# Scatterplot
fig = px.scatter(df, x=df.index, y='is_at_risk', 
                 labels={'index': 'Index', 'is_at_risk': 'Is at Risk'}, 
                 title='Scatter Plot of Individual "Is at Risk" Points')

# Update the y-axis labels
fig.update_yaxes(
    tickvals=[0, 1],
    ticktext=['No', 'Yes']
)

fig.show()

In [47]:
#Calculating the outliers
Q1 = df['is_at_risk'].quantile(0.25)
Q3 = df['is_at_risk'].quantile(0.75)
IQR = Q3 - Q1

lowerq = Q1
upperq = Q3

lower_bound = lowerq - (1.5 * IQR)
lower_bound
print(f"Values below {lower_bound} are lower outliers.")
upper_bound = upperq + (1.5 * IQR)
upper_bound
print(f"Values above {upper_bound} are upper outliers.")

Values below -1.5 are lower outliers.
Values above 2.5 are upper outliers.


In [ ]:
# identify outliers
threshold = 1.5
outliers = df[(df['is_at_risk'] < Q1 - threshold * IQR) | (df['is_at_risk'] > Q3 + threshold * IQR)]

# drop rows containing outliers
df_out = df.drop(outliers.index)

#plot
px.box(df_out, y='is_at_risk')

Preliminary Analysis:
- Present exploratory data analysis (EDA) to understand the dataset's structure, relationships, and key features.
- Include visualizations and summary statistics that support your preliminary findings.

Initial Results:
- Conduct initial tests of your models or analysis techniques.
- Provide a summary of the results, including any initial performance metrics or insights gained.
- Discuss any challenges encountered and how you addressed them.

In [26]:
#from hulearn.experimental.interactive import InteractiveCharts

In [ ]:
#clf = InteractiveCharts(df, labels='RiskPerformance')

In [ ]:
#from bokeh.io import output_notebook, show

In [ ]:
#clf.add_chart(x="NumTotalTrades", y="MaxDelqEver")

In [46]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

Next Steps:
- Outline the steps you plan to take to refine your approach and improve your results.
- Highlight any additional data you might need, further analyses, or alternative methodologies you are considering.